In [51]:
#create segment file
import os
import pathlib
import multiprocessing
import re

corpora = ['miami','siarad', 'patagonia']
base_dir = '/home/jiechi/ssd_home/data/codeswitch/bangortalk'


bash_files = []
# not_permitted = ['[/.]+<']
for corpus in corpora:
    corpus_dir = pathlib.Path(os.path.join(base_dir, corpus))
    wavscp = open(base_dir+'/' +corpus + 'wav.scp2','w', 1)
    fout = open(base_dir+'/' +corpus + 'text2','w', 1)
    utt2spk = open(base_dir + '/' +corpus + 'utt2spk2', 'w', 1)
    segment = open(base_dir + '/' +corpus + 'segments', 'w', 1) #utt_id file_id start_time end_time
    for audio in corpus_dir.iterdir():
        # bash_file = 'trim' + '_' + corpus +'_' + audio.name + '.sh'
        # bash_files.append(bash_file)
        # bash = open(bash_file,'w')
        # bash.writelines("#!/bin/bash\n")
        p = audio / 'split'
        p.mkdir(parents=True, exist_ok=True)
        #sox -c 1 -t wavpcm -e signed-integer .wav -t wavpcm - |
        wavscp.writelines(f"{corpus+'_'+ audio.name}\t sox -c 1 -t wavpcm -e signed-integer {os.path.join(str(audio), audio.name)}.wav -t wavpcm - |\n")
        chat_file = os.path.join(str(audio) , audio.name +'.cha')
        count = 0
        with open(chat_file, 'r') as f:
            for line in f:
                if 'Language markers:' in line:
                    # print(line)
                    m = re.search('(?<=Untagged words are )(\w+)', line).group(1)

                    if m == 'Spanish':
                        marker = 's'
                    elif m == 'English':
                        marker = 'e'

                    elif m == 'Welsh':
                        marker = 'w'
                if '\x15' in line and line[0] == '*':
                    if '[- spa]' in line:
                        m = 's'
                        line = line.replace('[- spa]', '')
                    elif '[- cym]' in line:
                        m = 'w'
                        line = line.replace('[- cym]', '')
                    elif '[- eng]' in line:
                        m = 'e'
                        line = line.replace('[- eng]', '')
                    else:
                        m = marker
                    count += 1
                    line = line.replace('\x15', '')
                    # print(marker)
                    # print(line)
                    line = re.sub("[\(\[].*?[\)\]]", "", line)
                    start, end = (line.split()[-1]).split('_')
                    speaker = line.split(':')[0][1::]
                    words = (line.split("\t")[1]).split()[0:-1]
                    #text = ' '.join((line.split(':')[1]).split()[0:-1])
                    text = []
                    for word in words[0:-1]:

                        if '@s:eng&spa' in word:
                            word = word.replace('@s:eng&spa', '')
                            word = 'esu_' + word

                        elif '@s:spa+cym' in word:
                            word = word.replace('@s:spa+cym', '')
                            word = 'sw_' + word

                        elif '@s:eng+spa' in word:
                            word = word.replace('@s:eng+spa', '')
                            word = 'es_' + word
                        elif '@s:spa+eng' in word:
                            word = word.replace('@s:spa+eng', '')
                            word = 'se_' + word
                        elif '@s:cym+spa' in word:
                            word = word.replace('@s:cym+spa', '')
                            word = 'ws_' + word
                        elif '@s:cym&spa' in word:
                            word = word.replace('@s:cym&spa', '')
                            word = 'wsu_' + word
                        elif '@s:cym&eng' in word:
                            word = word.replace('@s:cym&eng', '')
                            word = 'weu_' + word
                        elif '@s:spa' in word:
                            word = word.replace('@s:spa', '')
                            word = 's_' + word
                        elif '@s:eng' in word:
                            word = word.replace('@s:eng', '')
                            word = 'e_' + word
                        elif '@s:cym' in word:
                            word = word.replace('@s:cym', '')
                            word = 'w_' + word
                        else:
                            word = m + '_' + word
                        word = re.sub('\+eng','',word)
                        text.append(word)




                    utterid = speaker + '-' + audio.name + f'-{count:04}'
                    # print(utterid, ' '.join(text))
                    # break
                    fout.writelines(f"{utterid}\t{' '.join(text)}\n")
                    
                    utt2spk.writelines(f"{utterid}\t{speaker}-{audio.name}\n")
                    segment.writelines(f"{utterid}\t{corpus + '_' + audio.name}\t{int(start)/1000}\t{int(end)/1000}\n")
                    #f"{5:04}"
                    # cmd = f"ffmpeg -y -i {os.path.join(str(audio), audio.name + '.mp3')} -ss {int(start)/1000} -to {int(end)/1000} -ar 16000 {os.path.join(str(p), utterid)}.wav"
                    # print(cmd)
                    # bash.writelines(cmd + "\n")
# def worker(bash_file):
#     os.system(f"bash {bash_file}")

# jobs = []
# for i in bash_files:
#     p = multiprocessing.Process(target=worker, args=(i,))
#     jobs.append(p)
#     p.start()
# os.system("rm trim*.sh")


# test_dir = '/home/jiechi/ssd_home/data/codeswitch/bangortalk/patagonia/patagonia1'
# file_name = 'patagonia1'
# chat_file = os.path.join(test_dir, file_name + '.cha')
# p = pathlib.Path(os.path.join(test_dir , 'split'))
# p.mkdir(parents=True, exist_ok=True)
# lines = open(chat_file,'r').read().split("\n")
# fout = open(os.path.join(str(p), 'trans'),'w')

# for line in lines:
#     if '\x15' in line:
#         line = line.replace('\x15', '')
#         start, end = (line.split()[-1]).split('_')
#         speaker = line.split(':')[0][1::]
#         text = ' '.join((line.split(':')[1]).split()[0:-1])
#         print(line)
#         print(speaker, text)
#         utterid = file_name + f'-{5:04}'
#         print(start, end)
#         #f"{5:04}"
#         cmd = f"ffmpeg -i {os.path.join(test_dir, file_name + '.mp3')} -ss {int(start)/1000} -to {int(end)/1000} -ar 16000 {os.path.join(str(p), utterid)}.wav"
#         print(cmd)
#         bash.writelines(cmd + "\n")
#         break
# os.system(f"bash {bash_file}")

In [49]:
#filter only good english segments

corpora = ['miami','siarad', 'patagonia']
base_dir = '/home/jiechi/ssd_home/data/codeswitch/bangortalk'
for corpus in corpora:
    corpus_dir = pathlib.Path(os.path.join(base_dir, corpus))
    fout = open(base_dir+'/' +corpus + 'text2')
    utt2spk = open(base_dir + '/' +corpus + 'utt2spk2')
    segment = open(base_dir + '/' +corpus + 'segments') #utt_id file_id start_time end_time
    eng_text = open(base_dir+'/' +corpus + 'texten', 'w', 1)
    sp_text = open(base_dir+'/' +corpus + 'textsp', 'w', 1)
    cs_text = open(base_dir+'/' +corpus + 'textcs', 'w', 1)
    for i in fout:
        utterid, text = i.split("\t")
        words = text.split()
        tags = set()
        sent = []
        for word in words:
            tag = word.split("_")[0]
            tokens = word.split("_")[1::]
            if len(tokens) > 1:
                token = ' '.join(tokens)
            else:
                token = tokens[0]
            
            if ("&" not in token) and (token not in ['xxx', 'mmhm', 'www', 'mmm', 'uhuh']):
                ## not_permitted = ['[/.]+<']
                token = re.sub('\?|\.|\,|\!|\/|\;|\:|\[|\]|\+|\<|\\\|\>|\(|\)|\=|\"', '', token)
                
                if len(token) > 0 and (token not in ['xxx', 'mmhm', 'www', 'mmm']):
                    tags.add(tag)
                    sent.append(token.lower())
        if len(sent) > 0:
            
            if tags == set('e') or tags == set(['esu']) or tags == set(['e','esu']):
                print('eng')
                print(f"{' '.join(sent)}")
                eng_text.writelines(f"{utterid}\t{' '.join(sent)}\n")
            elif tags == set('s') or tags == set(['s', 'esu']):
                print('spanish')
                print(f"{' '.join(sent)}")
                sp_text.writelines(f"{utterid}\t{' '.join(sent)}\n")
            else:
                print('codeswitch')
                print(f"{' '.join(sent)}")
                cs_text.writelines(f"{utterid}\t{' '.join(sent)}\n")
        
            
            
        

eng
o k
spanish
y ya tú les preguntaste a todos los los los contrincantes
spanish
no puedes hablar en otras palabras ana
spanish
lo que dices no importa lo que digas
eng
amparito
spanish
para para proteger la identidad
spanish
el nobel se llama gabriela
spanish
y ya se acabó el pepperoni
spanish
ya voló
eng
oh
spanish
y cuánto tiempo ando con la vaina esta
eng
o k
codeswitch
para de un micrófono built in
spanish
mejor porque la vainita está colgando luego del
spanish
ay qué ay qué chulo
spanish
ay qué cosa más bella
eng
found him
spanish
me encanta lo wishy wiper
spanish
ah pues si no te sabes la canción te la te la tienen en
spanish
un ce de
codeswitch
es cute
spanish
tráelo
spanish
cuál es el tuyo
spanish
el mío el centro gallego el tuyo el capitolio y la
spanish
sí porque a ve a ve a veces a veces el el el lo único que tiene eh eh cuando hay problemas económicos que no se construye nada es que se salva la ciudad
spanish
ah pero es qué frescura
spanish
yo en la ca en la caja negra yo

spanish
y me pones esa porquería
spanish
cuatro
eng
oh not down either
codeswitch
el único que está down mira ya
spanish
blanco
spanish
y once
spanish
pues es buena gente
spanish
pues es buena gente
codeswitch
pero yo hay que play
spanish
voy a ser buena gente
spanish
así que no me no te pongas pesada
spanish
eh hace rato está sufriendo
spanish
sí
spanish
yo decía y a tu madre
spanish
tu no empezabas
eng
like mine is any better
spanish
mira al silencioso
spanish
y na más tiene dos fichas
spanish
el silencioso me acaba de tirar una mirada fulminante
eng
thomas
spanish
sí
spanish
dígame
spanish
sí el silencioso
eng
you have four
eng
four
spanish
dime jack
eng
yes you could have a banana
spanish
dale una banana a tu hermano
spanish
sí dale
spanish
dale
spanish
fue sin querer muñeca
eng
go over there
eng
get away from these chairs
codeswitch
dale un little banana
spanish
ya
eng
i don't know if there's any
spanish
ve y fíjate
spanish
soy la única cabezona de la casa
spanish
lo demás son tod

eng
if he can draw
eng
you know and then otto wagner's drawings were just like ahhh you know
eng
but hoffmann's he's the one who
eng
he's the one that did all those beautiful round buildings
eng
you know he wasn't he was a little bit less busy than than than wagner
eng
she but he couldn't
eng
i mean and he did like restaurants
eng
and he even did
eng
he had sketches for the menu for the for the silverware the flatware the furniture
eng
i mean it was a comprehensive like it used to be but he couldn't draw worth a damn
eng
you know they were like you know fifth grader drawings
eng
draw by hand
eng
ah yes i have
eng
he still follows the old fashioned
eng
he's just the the prit he's just got an award the pritzker i think he's just had the pritzker
eng
santiago calatrava
eng
calatrava still draws like that
eng
oh really
eng
i didn't know that either
eng
well calatrava's like that
eng
he draws
eng
you weren't here
eng
well you were downstairs when i came back from the las vegas
eng
five
eng


eng
where have you been
eng
i was swimming
eng
but i couldn't hear you
eng
oh i didn't hear you
eng
good job you closed
spanish
mami
eng
marga close the door with the handle
eng
really the crazy tiger was outside
eng
turn the handle
eng
there we go
eng
you gonna sit with us
eng
yeah
eng
what were you watching on t v
eng
ah
eng
what
eng
hannah montana
eng
hannah montana
spanish
mami
eng
yes
eng
i'm putting my foot up for a reason
eng
put your foot up
eng
you have cute toes
eng
they look like dad's
eng
uh uh
spanish
dile como mami
codeswitch
do your toes look like mami or papi
spanish
mami
eng
yeah
codeswitch
and papi
spanish
no
codeswitch
mami's
spanish
mami
eng
yeah
eng
i wanna play over there
eng
where
eng
now go there a little bit
eng
you know where the cats were
eng
they were under the deck
eng
where
eng
down here under this
eng
i guess they were trying to find protection
eng
protection
eng
don't you remember those shells when they need a protection
eng
yeah
eng
the one inside the s

eng
satia saibaba
spanish
saibaba es muy conocido en india
spanish
es que en india hay hay más de mil religiones reconocidas
spanish
sí sí
eng
and and then i just read that er i wasn't able to find god or find inner peace
eng
so i just eventually stopped looking
eng
and i became a rebel
eng
and i just told
spanish
un rebelde sin causa
eng
yeah like just told jesus or whatever god or representation there was at that time in my mind
eng
it's o k i'm just tired of looking for you
eng
and i got nothing
eng
i feel nothing
eng
i i haven't got any more faith
eng
so i'm just going to stop looking
eng
if you want to see me just look for me
eng
so i'm not going to look for you
eng
um i don't know
eng
then i became a atheist and then agnostic and plenty of stuff
eng
and then i came here to the u s seven years ago
eng
and attend like christian meetings and christian churches and stuff
spanish
protestante
codeswitch
yeah protestante
eng
and at the end i just realised that i am just a catholic perso

...

codeswitch
be lle dan ni n byw
codeswitch
dan ni n byw yn nhrelew
codeswitch
fan hyn trelew
codeswitch
ia
codeswitch
en xxx siete casa dos ochenta y cuatro
codeswitch
tŷ ddau cant wyth deg pedwar
codeswitch
a ti n licio wyt ti n licio fyw yn fan hyn
codeswitch
na
codeswitch
pam
codeswitch
achos dw i isio um byw yn y gaiman
codeswitch
pam
codeswitch
achos dw i efo teulu yn y gaiman
codeswitch
a dw i wneud bopeth yn gaiman
codeswitch
mm
codeswitch
dw i n dawn dw i n dysgu dawnsio yn gaiman
codeswitch
dw i n dysgu uh canu yn gaiman
codeswitch
a dw i n dysgu chwarae piano yn gaiman
codeswitch
a
codeswitch
a dw i isio bod yn gaiman
codeswitch
achos dw i n conocer gaiman
codeswitch
ti nabod
codeswitch
dw i nabod gaiman a trelew tipyn bach
codeswitch
dw i yn gaiman dw i n gallu mynd gan cerdded i rywle yn trelew na
codeswitch
hym
codeswitch
i lle i lle wyt ti n mynd yng nghym yn y gaiman
codeswitch
uh i tŷ nain
codeswitch
i tŷ hen nain
codeswitch
i tŷ mm mabli
codeswitch
i tŷ anti natalia
cod

spanish
ocho por cuatro treinta y dos
spanish
cuatro empanadas cada una
spanish
trescientas empanadas
codeswitch
faint ydy hynna
codeswitch
ugain
codeswitch
dwsin empanadas
codeswitch
uh trescientas empanadas
codeswitch
nage
codeswitch
mwy
codeswitch
a beth arall oedd wil yn mynd i ofyn i i bobl ydy uh i nhw ddewis rhwng mynd â empanadas a mynd â uh tarta
spanish
tartas
codeswitch
be i gosod y ddau beth ar y bwrdd
codeswitch
ia
codeswitch
gosod y ddau beth ar y bwrdd ia
codeswitch
a ddim dim pwdin felly
codeswitch
mae siŵr
codeswitch
heb bwdin
codeswitch
naci
codeswitch
pwdin dim pwdin
codeswitch
na no
codeswitch
eh bydd yn ofalus efo r peth na
codeswitch
ia achos hefyd oedden nhw n mynd i ofyn i wel dim ond i bobl y côr felly aros
codeswitch
a bobl yr ysgol gerdd i aros
codeswitch
i gael bwyd efo nhw
codeswitch
ddim gweddill y bobl fydd yn mynd i r
codeswitch
i r cyngerdd
codeswitch
i r cyngerdd
codeswitch
sí oh
codeswitch
ia fy rhaid peidio cyhoeddi r peth yn lle
codeswitch
na
codesw

codeswitch
gustavo perez a ivette sanchez
codeswitch
enw bach neis
codeswitch
ond hŷn na fo
codeswitch
ivette sanchez
codeswitch
sanchez
codeswitch
dw i ddim yn gwybod lle maen nhw wedi cael hwnna
codeswitch
ivette sanchez
codeswitch
ond na fo
codeswitch
ah sanchez meddyliwch chi
codeswitch
sanchez
codeswitch
wel na fo
codeswitch
ond oeddwn i yn deud
codeswitch
tad a eu mam sy ar
codeswitch
debyg iawn
codeswitch
oedden ni yn oedden nhw n mynd i roi selena neu selene arni
codeswitch
ond oeddwn i yn licio yr
codeswitch
no ond na fo
codeswitch
selene ydy um lloer ynde
spanish
la luna
codeswitch
selene yn sôn am
codeswitch
sí selene
codeswitch
dw i dw i m yn gwybod os dw i yn dw i m yn nabod neb efo yr enw yna deud y gwir
codeswitch
ond na fo
codeswitch
ond dw i wedi gweld o mewn barddoniaeth dw i n credu
codeswitch
ond r un fath â cynthia ynde
codeswitch
um
codeswitch
dach chi di cael sgwrs efo socorro alvarez ar ôl iddi fod
codeswitch
na na dw i m wedi cael ddim wedi cael sgwrs
codeswitc

codeswitch
a r y y llo n dechrau a r gwartheg yn dechrau dod o r o r gwaelod
codeswitch
ar garlam rŵan
codeswitch
clywed y lloi yn brefu
codeswitch
welaist di
codeswitch
gwartheg yn dod ar y uh ar garlam eh
codeswitch
o r gwaelod y ffarm
codeswitch
ie
codeswitch
achos clywed y lloi yn brefu
codeswitch
ie
codeswitch
achos bod rhain ar eu cefnau nhw
codeswitch
a mi neidiodd un fuwch yr weiar bigog
codeswitch
a mi dorrodd y pedwar peth
codeswitch
o
codeswitch
o
codeswitch
achos wnaeth dada a mam rioed curo ni
codeswitch
curo roi
codeswitch
ie
codeswitch
curo
codeswitch
drefn do drefn drefn do
codeswitch
curo ia chwip din
codeswitch
do siŵr
codeswitch
do drefn do do
codeswitch
siŵr o fod
codeswitch
ajá ie
codeswitch
i rhoi ni yn ein lle
codeswitch
mm
codeswitch
ac uh ond diwrnod hwnnw mi gaeth y ddau yma gweir
codeswitch
achos gorfod nhw ladd y fuwch achos oedd uh oedd i n mynd uh oedd hi wedi wedi mynd mewn gwaed ynde
codeswitch
mewn mewn gwaed
codeswitch
o
codeswitch
wedi gwaedu
codeswit

codeswitch
ie
codeswitch
a a mae athrawon yr ysgol feithrin mynd i r ysgol dau ddeg pedwar
codeswitch
o r ysgol feithrin
spanish
eso es relindo
spanish
bueno
codeswitch
ah
codeswitch
mae mae mae hi maen nhw hapus iawn con la experiencia
spanish
sí
codeswitch
ah fue enriquecedora
codeswitch
sacaron muchas cosas eh positivas eh
spanish
sí sí sí sí sí sí
spanish
qué bueno
codeswitch
wn i dim rŵan
codeswitch
wel está bien
codeswitch
a ti pan wyt ti n dod o yr ysgol blwyddyn diwetha blwyddyn nesa
codeswitch
mis mawrth dw i n credu ia
codeswitch
dau ar hugain
codeswitch
ah
spanish
veintidós o por ahí veintidós
codeswitch
ardderchog
codeswitch
ia
codeswitch
a mae heledd eh renuncia yn mis eh chwefror achos mae
codeswitch
sut wyt ti n gwybod
codeswitch
eh
codeswitch
sut wyt ti n gwybod mae hi n
codeswitch
dywedais hi i ti
codeswitch
ie
codeswitch
achos mae
codeswitch
mae hi n mynd yn ôl i drelew
codeswitch
fy
codeswitch
ie
codeswitch
ei ei gariad hi
codeswitch
uh wedi symud
codeswitch
wedi sym

In [22]:
re.sub("\ |\?|\.|\!|\/|\;|\:|\[|\]|\+|\<|\'|\\\|\>", '', "[?]")


''

{'esu'}
{'s', 'u', 'e'}


True

   2579 cs 1879 250 500
  29813 en 20813  3000 6000
  12579 sp 7789 1250 2500
  44971 total
  